In [ ]:
import os
import requests
import pandas as pd
from bs4 import BeautifulSoup
import re

url_template = "https://www.ad.co.il/archive/nadlanrent?sp275=17413&view=list&pageindex={}"
output_dir = "real_estate_data"

# Create output directory if it does not exist
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

def extract_name(soup):
    name_div = soup.find('span', class_='ms-2 my-0 pb-1 fs-1 text-1100')
    name = name_div.text.strip() if name_div else None

    if not name:
        alt_name_div = soup.find('p', class_='ms-2 my-0 text-dark')
        name = alt_name_div.text.strip() if alt_name_div else None

    if not name:
        alt_name_div = soup.find('p', class_='ms-2 my-0 text-dark')
        name = alt_name_div.text.strip() if alt_name_div else "N/A"

    return name

def scrape_and_save(start_page, end_page):
    data_ids = []

    for page in range(start_page, end_page+1):
        url = url_template.format(page)
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/113.0.0.0 Safari/537.36'
        }
        response = requests.get(url, headers=headers)
        if response.status_code == 200:
            soup = BeautifulSoup(response.text, 'html.parser')
            ads = soup.find_all(attrs={"data-id": True})
            data_ids.extend([ad.get('data-id') for ad in ads])
            print(f"Page {page}: {len(ads)} ads found")
        else:
            print(f"Error scraping page {page}: {response.text}")

    extracted_details = []

    for data_id in data_ids:
        link = f"https://www.ad.co.il/ad/{data_id}"
        response = requests.get(link)
        if response.status_code == 200:
            soup = BeautifulSoup(response.text, 'html.parser')
            details_table = soup.find('table', class_='table table-sm mb-4')
            if details_table:
                details = {}
                rows = details_table.find_all('tr')
                for row in rows:
                    cells = row.find_all('td')
                    if len(cells) == 2:
                        key = cells[0].text.strip()
                        value = cells[1].text.strip()
                        details[key] = value

                ad_type = details.get('פרטי הנכס')
                area = details.get('אזור')
                city = details.get('עיר')
                street = details.get('שכונה')
                address = details.get('כתובת')
                number_of_rooms = details.get('חדרים')
                size = details.get('שטח בנוי')
                floor = details.get('קומה')
                property_tax = details.get('ארנונה בחודש')
                house_committee = details.get('ועד בית בחודש')

                date_divs = soup.find_all('div', class_='px-3')
                creation_date = next((div.text.replace("תאריך יצירה:", "").strip() for div in date_divs if "תאריך יצירה" in div.text), "N/A")

                price_divs = soup.find_all('h2', class_='card-title')
                price_text = price_divs[1].text.strip() if len(price_divs) > 1 else "N/A"
                price_match = re.search(r'\d{1,3}(?:,\d{3})+', price_text)
                price = price_match.group().replace(',', '') if price_match else "N/A"

                phone_button = soup.find('button', onclick=re.compile(r"showPhone\(this, (\d+),'(.*?)',true\)"))
                phone_number = phone_button['onclick'].split("'")[1] if phone_button else "N/A"

                text_div = soup.find('div', class_='p-3')
                text_paragraph = text_div.find('p', class_='text-word-break') if text_div else None
                text = text_paragraph.text.strip().replace('\n', '') if text_paragraph else "N/A"

                # Extract the name "נועם"
                name = extract_name(soup)

                card_icons_div = soup.find('div', class_='card-icons flex-wrap d-flex h-100')
                feature_elements = card_icons_div.find_all('div', class_='card-icon col-6 d-inline')

                features = {
                    "מרפסת": 0,
                    "חניה": 0,
                    "מעלית": 0,
                    "מזגן": 0,
                    "מחסן": 0,
                    "משופצת": 0,
                    "מרפסת שמש": 0  # New feature
                }

                for element in feature_elements:
                    feature_name = element.find('span').text.strip()
                    feature_value = 1 if "fa-check" in element.find('i')['class'] else 0
                    if feature_name in features:
                        features[feature_name] = feature_value

                extracted_details.append({
                    'Type': ad_type,
                    'Area': area,
                    'City': city,
                    'Street': street,
                    'Address': address,
                    'Number of Rooms': number_of_rooms,
                    'Size': size,
                    'Personal Link': link,
                    'Date Post': creation_date,
                    'Price': price,
                    'Phone Number': phone_number,
                    'Floor': floor,
                    'Property Tax': property_tax,
                    'House Committee': house_committee,
                    'Text': text,
                    'Name': name,
                    **features  # Add the extracted features to the dictionary
                })
                print(f"Details extracted from {link}")
            else:
                print(f"No details found for {link}")
        else:
            print(f"Error accessing {link}")

    df = pd.DataFrame(extracted_details)
    sorted_df = df.sort_values(by='Date Post')
    sorted_df = sorted_df.reset_index(drop=True)

    excel_file = f"scraped_data_{start_page}-{end_page}.xlsx"
    sorted_df.to_excel(os.path.join(output_dir, excel_file), index=False, encoding='utf-8-sig')
    print(f"DataFrame saved to {excel_file}")

# Specify the total number of pages you want to scrape
total_pages = 5737

num_pages_per_batch = 50
for batch_start in range(1, total_pages+1, num_pages_per_batch):
    batch_end = min(batch_start + num_pages_per_batch - 1, total_pages)
    scrape_and_save(batch_start, batch_end)


Page 1: 48 ads found
Page 2: 48 ads found
Page 3: 48 ads found
Page 4: 48 ads found
Page 5: 48 ads found
Page 6: 48 ads found
Page 7: 48 ads found
Page 8: 48 ads found
Page 9: 48 ads found
Page 10: 48 ads found
Page 11: 48 ads found
Page 12: 48 ads found
Page 13: 48 ads found
Page 14: 48 ads found
Page 15: 48 ads found
Page 16: 48 ads found
Page 17: 48 ads found
Page 18: 48 ads found
Page 19: 48 ads found
Page 20: 48 ads found
Page 21: 48 ads found
Page 22: 48 ads found
Page 23: 48 ads found
Page 24: 48 ads found
Page 25: 48 ads found
Page 26: 48 ads found
Page 27: 48 ads found
Page 28: 48 ads found
Page 29: 48 ads found
Page 30: 48 ads found
Page 31: 48 ads found
Page 32: 48 ads found
Page 33: 48 ads found
Page 34: 48 ads found
Page 35: 48 ads found
Page 36: 48 ads found
Page 37: 48 ads found
Page 38: 48 ads found
Page 39: 48 ads found
Page 40: 48 ads found
Page 41: 48 ads found
Page 42: 48 ads found
Page 43: 48 ads found
Page 44: 48 ads found
Page 45: 48 ads found
Page 46: 48 ads fou

### scraping from page *Start_Page_After_Crash* and continue in batches of 50 until page 5737. Here's the updated code:

In [4]:
import os
import requests
import pandas as pd
from bs4 import BeautifulSoup
import re

url_template = "https://www.ad.co.il/archive/nadlanrent?sp275=17413&view=list&pageindex={}"
output_dir = "real_estate_data"

# Create output directory if it does not exist
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

def extract_name(soup):
    name_div = soup.find('span', class_='ms-2 my-0 pb-1 fs-1 text-1100')
    name = name_div.text.strip() if name_div else None

    if not name:
        alt_name_div = soup.find('p', class_='ms-2 my-0 text-dark')
        name = alt_name_div.text.strip() if alt_name_div else None

    if not name:
        alt_name_div = soup.find('p', class_='ms-2 my-0 text-dark')
        name = alt_name_div.text.strip() if alt_name_div else "N/A"

    return name

def scrape_and_save(start_page, end_page):
    data_ids = []

    for page in range(start_page, end_page+1):
        url = url_template.format(page)
        headers = {
            'User-Agent': 'Mozilla/5.0 (Windows NT 10.0) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/113.0.0.0 Safari/537.36'
        }
        response = requests.get(url, headers=headers)
        if response.status_code == 200:
            soup = BeautifulSoup(response.text, 'html.parser')
            ads = soup.find_all(attrs={"data-id": True})
            data_ids.extend([ad.get('data-id') for ad in ads])
            print(f"Page {page}: {len(ads)} ads found")
        else:
            print(f"Error scraping page {page}: {response.text}")

    extracted_details = []

    for data_id in data_ids:
        link = f"https://www.ad.co.il/ad/{data_id}"
        response = requests.get(link)
        if response.status_code == 200:
            soup = BeautifulSoup(response.text, 'html.parser')
            details_table = soup.find('table', class_='table table-sm mb-4')
            if details_table:
                details = {}
                rows = details_table.find_all('tr')
                for row in rows:
                    cells = row.find_all('td')
                    if len(cells) == 2:
                        key = cells[0].text.strip()
                        value = cells[1].text.strip()
                        details[key] = value

                ad_type = details.get('פרטי הנכס')
                area = details.get('אזור')
                city = details.get('עיר')
                street = details.get('שכונה')
                address = details.get('כתובת')
                number_of_rooms = details.get('חדרים')
                size = details.get('שטח בנוי')
                floor = details.get('קומה')
                property_tax = details.get('ארנונה בחודש')
                house_committee = details.get('ועד בית בחודש')

                date_divs = soup.find_all('div', class_='px-3')
                creation_date = next((div.text.replace("תאריך יצירה:", "").strip() for div in date_divs if "תאריך יצירה" in div.text), "N/A")

                price_divs = soup.find_all('h2', class_='card-title')
                price_text = price_divs[1].text.strip() if len(price_divs) > 1 else "N/A"
                price_match = re.search(r'\d{1,3}(?:,\d{3})+', price_text)
                price = price_match.group().replace(',', '') if price_match else "N/A"

                phone_button = soup.find('button', onclick=re.compile(r"showPhone\(this, (\d+),'(.*?)',true\)"))
                phone_number = phone_button['onclick'].split("'")[1] if phone_button else "N/A"

                text_div = soup.find('div', class_='p-3')
                text_paragraph = text_div.find('p', class_='text-word-break') if text_div else None
                text = text_paragraph.text.strip().replace('\n', '') if text_paragraph else "N/A"

                # Extract the name "נועם"
                name = extract_name(soup)

                card_icons_div = soup.find('div', class_='card-icons flex-wrap d-flex h-100')
                feature_elements = card_icons_div.find_all('div', class_='card-icon col-6 d-inline')

                features = {
                    "מרפסת": 0,
                    "חניה": 0,
                    "מעלית": 0,
                    "מזגן": 0,
                    "מחסן": 0,
                    "משופצת": 0,
                    "מרפסת שמש": 0  # New feature
                }

                for element in feature_elements:
                    feature_name = element.find('span').text.strip()
                    feature_value = 1 if "fa-check" in element.find('i')['class'] else 0
                    if feature_name in features:
                        features[feature_name] = feature_value

                extracted_details.append({
                    'Type': ad_type,
                    'Area': area,
                    'City': city,
                    'Street': street,
                    'Address': address,
                    'Number of Rooms': number_of_rooms,
                    'Size': size,
                    'Personal Link': link,
                    'Date Post': creation_date,
                    'Price': price,
                    'Phone Number': phone_number,
                    'Floor': floor,
                    'Property Tax': property_tax,
                    'House Committee': house_committee,
                    'Text': text,
                    'Name': name,
                    **features  # Add the extracted features to the dictionary
                })
                print(f"Details extracted from {link}")
            else:
                print(f"No details found for {link}")
        else:
            print(f"Error accessing {link}")

    df = pd.DataFrame(extracted_details)
    sorted_df = df.sort_values(by='Date Post')
    sorted_df = sorted_df.reset_index(drop=True)

    excel_file = f"scraped_data_{start_page}-{end_page}.xlsx"
    sorted_df.to_excel(os.path.join(output_dir, excel_file), index=False, encoding='utf-8-sig')
    print(f"DataFrame saved to {excel_file}")

# Specify the total number of pages you want to scrape
start_page = 4101
end_page = 5737
batch_size = 50

for batch_start in range(start_page, end_page+1, batch_size):
    batch_end = min(batch_start + batch_size - 1, end_page)
    scrape_and_save(batch_start, batch_end)


Page 4101: 48 ads found
Page 4102: 48 ads found
Page 4103: 48 ads found
Page 4104: 48 ads found
Page 4105: 48 ads found
Page 4106: 48 ads found
Page 4107: 48 ads found
Page 4108: 48 ads found
Page 4109: 48 ads found
Page 4110: 48 ads found
Page 4111: 48 ads found
Page 4112: 48 ads found
Page 4113: 48 ads found
Page 4114: 48 ads found
Page 4115: 48 ads found
Page 4116: 48 ads found
Page 4117: 48 ads found
Page 4118: 48 ads found
Page 4119: 48 ads found
Page 4120: 48 ads found
Page 4121: 48 ads found
Page 4122: 48 ads found
Page 4123: 48 ads found
Page 4124: 48 ads found
Page 4125: 48 ads found
Page 4126: 48 ads found
Page 4127: 48 ads found
Page 4128: 48 ads found
Page 4129: 48 ads found
Page 4130: 48 ads found
Page 4131: 48 ads found
Page 4132: 48 ads found
Page 4133: 48 ads found
Page 4134: 48 ads found
Page 4135: 48 ads found
Page 4136: 48 ads found
Page 4137: 48 ads found
Page 4138: 48 ads found
Page 4139: 48 ads found
Page 4140: 48 ads found
Page 4141: 48 ads found
Page 4142: 48 ad

C:\Users\dell\anaconda3\lib\site-packages\pandas\util\_decorators.py:211: FutureWarning: the 'encoding' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'encoding'
  return func(*args, **kwargs)
<ipython-input-4-1c8eaa588cd8>:141: UserWarning: Pandas requires version '1.4.3' or newer of 'xlsxwriter' (version '1.3.8' currently installed).
  sorted_df.to_excel(os.path.join(output_dir, excel_file), index=False, encoding='utf-8-sig')


DataFrame saved to scraped_data_4101-4150.xlsx
Page 4151: 48 ads found
Page 4152: 48 ads found
Page 4153: 48 ads found
Page 4154: 48 ads found
Page 4155: 48 ads found
Page 4156: 48 ads found
Page 4157: 48 ads found
Page 4158: 48 ads found
Page 4159: 48 ads found
Page 4160: 48 ads found
Page 4161: 48 ads found
Page 4162: 48 ads found
Page 4163: 48 ads found
Page 4164: 48 ads found
Page 4165: 48 ads found
Page 4166: 48 ads found
Page 4167: 48 ads found
Page 4168: 48 ads found
Page 4169: 48 ads found
Page 4170: 48 ads found
Page 4171: 48 ads found
Page 4172: 48 ads found
Page 4173: 48 ads found
Page 4174: 48 ads found
Page 4175: 48 ads found
Page 4176: 48 ads found
Page 4177: 48 ads found
Page 4178: 48 ads found
Page 4179: 48 ads found
Page 4180: 48 ads found
Page 4181: 48 ads found
Page 4182: 48 ads found
Page 4183: 48 ads found
Page 4184: 48 ads found
Page 4185: 48 ads found
Page 4186: 48 ads found
Page 4187: 48 ads found
Page 4188: 48 ads found
Page 4189: 48 ads found
Page 4190: 48 ads

C:\Users\dell\anaconda3\lib\site-packages\pandas\util\_decorators.py:211: FutureWarning: the 'encoding' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'encoding'
  return func(*args, **kwargs)
<ipython-input-4-1c8eaa588cd8>:141: UserWarning: Pandas requires version '1.4.3' or newer of 'xlsxwriter' (version '1.3.8' currently installed).
  sorted_df.to_excel(os.path.join(output_dir, excel_file), index=False, encoding='utf-8-sig')


DataFrame saved to scraped_data_4151-4200.xlsx
Page 4201: 48 ads found
Page 4202: 48 ads found
Page 4203: 48 ads found
Page 4204: 48 ads found
Page 4205: 48 ads found
Page 4206: 48 ads found
Page 4207: 48 ads found
Page 4208: 48 ads found
Page 4209: 48 ads found
Page 4210: 48 ads found
Page 4211: 48 ads found
Page 4212: 48 ads found
Page 4213: 48 ads found
Page 4214: 48 ads found
Page 4215: 48 ads found
Page 4216: 48 ads found
Page 4217: 48 ads found
Page 4218: 48 ads found
Page 4219: 48 ads found
Page 4220: 48 ads found
Page 4221: 48 ads found
Page 4222: 48 ads found
Page 4223: 48 ads found
Page 4224: 48 ads found
Page 4225: 48 ads found
Page 4226: 48 ads found
Page 4227: 48 ads found
Page 4228: 48 ads found
Page 4229: 48 ads found
Page 4230: 48 ads found
Page 4231: 48 ads found
Page 4232: 48 ads found
Page 4233: 48 ads found
Page 4234: 48 ads found
Page 4235: 48 ads found
Page 4236: 48 ads found
Page 4237: 48 ads found
Page 4238: 48 ads found
Page 4239: 48 ads found
Page 4240: 48 ads

...

DataFrame saved to scraped_data_5601-5650.xlsx
Page 5651: 48 ads found
Page 5652: 48 ads found
Page 5653: 48 ads found
Page 5654: 48 ads found
Page 5655: 48 ads found
Page 5656: 48 ads found
Page 5657: 48 ads found
Page 5658: 48 ads found
Page 5659: 48 ads found
Page 5660: 48 ads found
Page 5661: 48 ads found
Page 5662: 48 ads found
Page 5663: 48 ads found
Page 5664: 48 ads found
Page 5665: 48 ads found
Page 5666: 48 ads found
Page 5667: 48 ads found
Page 5668: 48 ads found
Page 5669: 48 ads found
Page 5670: 48 ads found
Page 5671: 48 ads found
Page 5672: 48 ads found
Page 5673: 48 ads found
Page 5674: 48 ads found
Page 5675: 48 ads found
Page 5676: 48 ads found
Page 5677: 48 ads found
Page 5678: 48 ads found
Page 5679: 48 ads found
Page 5680: 48 ads found
Page 5681: 48 ads found
Page 5682: 48 ads found
Page 5683: 48 ads found
Page 5684: 48 ads found
Page 5685: 48 ads found
Page 5686: 48 ads found
Page 5687: 48 ads found
Page 5688: 48 ads found
Page 5689: 48 ads found
Page 5690: 48 ads

C:\Users\dell\anaconda3\lib\site-packages\pandas\util\_decorators.py:211: FutureWarning: the 'encoding' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'encoding'
  return func(*args, **kwargs)
<ipython-input-4-1c8eaa588cd8>:141: UserWarning: Pandas requires version '1.4.3' or newer of 'xlsxwriter' (version '1.3.8' currently installed).
  sorted_df.to_excel(os.path.join(output_dir, excel_file), index=False, encoding='utf-8-sig')


DataFrame saved to scraped_data_5651-5700.xlsx
Page 5701: 48 ads found
Page 5702: 48 ads found
Page 5703: 48 ads found
Page 5704: 48 ads found
Page 5705: 48 ads found
Page 5706: 48 ads found
Page 5707: 48 ads found
Page 5708: 48 ads found
Page 5709: 48 ads found
Page 5710: 48 ads found
Page 5711: 48 ads found
Page 5712: 48 ads found
Page 5713: 48 ads found
Page 5714: 48 ads found
Page 5715: 48 ads found
Page 5716: 48 ads found
Page 5717: 48 ads found
Page 5718: 48 ads found
Page 5719: 48 ads found
Page 5720: 48 ads found
Page 5721: 48 ads found
Page 5722: 48 ads found
Page 5723: 48 ads found
Page 5724: 48 ads found
Page 5725: 48 ads found
Page 5726: 48 ads found
Page 5727: 48 ads found
Page 5728: 48 ads found
Page 5729: 48 ads found
Page 5730: 48 ads found
Page 5731: 48 ads found
Page 5732: 48 ads found
Page 5733: 48 ads found
Page 5734: 48 ads found
Page 5735: 48 ads found
Page 5736: 48 ads found
Page 5737: 48 ads found
Details extracted from https://www.ad.co.il/ad/3490157
Details ex

C:\Users\dell\anaconda3\lib\site-packages\pandas\util\_decorators.py:211: FutureWarning: the 'encoding' keyword is deprecated and will be removed in a future version. Please take steps to stop the use of 'encoding'
  return func(*args, **kwargs)
<ipython-input-4-1c8eaa588cd8>:141: UserWarning: Pandas requires version '1.4.3' or newer of 'xlsxwriter' (version '1.3.8' currently installed).
  sorted_df.to_excel(os.path.join(output_dir, excel_file), index=False, encoding='utf-8-sig')


DataFrame saved to scraped_data_5701-5737.xlsx
